In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import math
from sklearn.metrics import accuracy_score
from sklearn import metrics
from sklearn.metrics import confusion_matrix
import sys,os
sys.path.append(r"C:\Users\anai\dive\oreilly\deep-learning-from-scratch\common")
from util import im2col, col2im

In [2]:
sys.path

['',
 'C:\\Users\\anai\\Anaconda3\\python36.zip',
 'C:\\Users\\anai\\Anaconda3\\DLLs',
 'C:\\Users\\anai\\Anaconda3\\lib',
 'C:\\Users\\anai\\Anaconda3',
 'C:\\Users\\anai\\AppData\\Roaming\\Python\\Python36\\site-packages',
 'C:\\Users\\anai\\Anaconda3\\lib\\site-packages',
 'C:\\Users\\anai\\Anaconda3\\lib\\site-packages\\win32',
 'C:\\Users\\anai\\Anaconda3\\lib\\site-packages\\win32\\lib',
 'C:\\Users\\anai\\Anaconda3\\lib\\site-packages\\Pythonwin',
 'C:\\Users\\anai\\Anaconda3\\lib\\site-packages\\IPython\\extensions',
 'C:\\Users\\anai\\.ipython',
 'C:\\Users\\anai\\dive\\oreilly\\deep-learning-from-scratch\\common']

【問題1】2次元畳み込み層の作成 
1次元畳み込み層のクラスConv1dを発展させ、2次元畳み込み層のクラスConv2dを作成してください。
フォワードプロパゲーションの数式は以下のようになります。

【問題2】2次元畳み込み後の出力サイズ 
畳み込みを行うと特徴マップのサイズが変化します。どのように変化するかは以下の数式から求められます。
この計算を行う関数を作成してください。

In [3]:
class Conv2d:
    """
    ノード数n_nodes1からn_nodes2への全結合層
    Parameters
    ----------
    n_nodes1 : int
      前の層のノード数
    n_nodes2 : int
      後の層のノード数
    initializer : 初期化方法のインスタンス
    optimizer : 最適化手法のインスタンス
    """
    def __init__(self):
        self.P = 0
        self.Str = 1
        self.a = np.array([])
        self.dW = np.array([])
        self.dX = np.array([])
        #self.s=None
        
    def forward(self, X, W ,B):
        """
        フォワード
        Parameters
        ----------
        X : 次の形のndarray, shape (batch_size, n_nodes_bf)
            入力
        Returns
        ----------
        A : 次の形のndarray, shape (batch_size, n_nodes_af)
            出力
        """
        self.X = X
        self.XN, self.XC, self.XH, self.XW = self.X.shape
        
        self.W = W 
        self.FN, self.FC, self.FH, self.FW = self.W.shape
        self.B = B
        self.s = self.W.shape[3]
        
        self._output_size()
        
        self.Wre = self.W.reshape(self.FN,-1)
        #self.Bre = np.array([self.B] * self.Nhout * self.Nwout).reshape(-1,1)
        self.Bre = self.B.reshape(1,-1)
        self.col = im2col(self.X , self.FH, self.FW, self.Str, self.P)
        
        display(self.col)
        display(self.Wre.T)
        #display(self.Bre)
        display(self.col @ self.Wre.T)
        self.Are = (self.col @ self.Wre.T) + self.Bre
        display(self.Are)
        self.a = self.Are.reshape(self.XN, self.Nhout, self.Nwout,-1).transpose(0,3,1,2)
        display(self.a.shape)
        return self.a
    
    def _output_size(self):
        self.Nhout = int((self.XH + 2*self.P - self.FH) / self.Str + 1)       
        self.Nwout = int((self.XW + 2*self.P - self.FW) / self.Str + 1)
        
    def backward(self, dA):
        """
        バックワード
        Parameters
        ----------
        dA : 次の形のndarray, shape (batch_size, n_nodes2)
            後ろから流れてきた勾配
        Returns
        ----------
        dZ : 次の形のndarray, shape (batch_size, n_nodes1)
            前に流す勾配
        """
        self.dA=dA.transpose(0,2,3,1).reshape(-1,self.FN)
        self.dB = np.sum(self.dA, axis=0)
        
        display(self.dA)
        display(self.col.T)
        self.dW = np.dot(self.col.T , self.dA)
        display(self.dW)
        self.dW = self.dW.transpose(1, 0).reshape(self.FN, self.FC, self.FH, self.FW)
        display(self.dW)
        
        self.dXre = np.dot(self.dA, self.Wre) 
        self.dX = col2im(self.dXre, self.X.shape, self.FH, self.FW, self.Str, self.P)

        return self.dX
    

In [4]:
x = np.array([[2, 3, 4, 5], [1, 2, 3, 4]]) # shape(2, 4)で、（入力チャンネル数、特徴量数）である。
w = np.array([[[[1,1,1],
            [1,1,1]],
            [[1,1,1],
            [2,1,1]],
            [[2,1,1],
            [1,1,2]]]])
w=w.transpose(1,0,2,3)
display(w.shape)
b = np.array([3, 2, 1]) # （出力チャンネル数）
b=np.array([b]*1)
x = np.array([[x]*1]*1)
x.shape

(3, 1, 2, 3)

(1, 1, 2, 4)

In [5]:
dnn2 = Conv2d()
dnn2.forward(x,w,b)

array([[2., 3., 4., 1., 2., 3.],
       [3., 4., 5., 2., 3., 4.]])

array([[1, 1, 2],
       [1, 1, 1],
       [1, 1, 1],
       [1, 2, 1],
       [1, 1, 1],
       [1, 1, 2]])

array([[15., 16., 20.],
       [21., 23., 28.]])

array([[18., 18., 21.],
       [24., 25., 29.]])

(1, 3, 1, 2)

array([[[[18., 24.]],

        [[18., 25.]],

        [[21., 29.]]]])

In [6]:
dA = np.array([[[52,56]],
            [[32,35]],
            [[9,11]]])
dA = np.array([dA]*1)
dA.shape

(1, 3, 1, 2)

In [7]:
dnn2.backward(dA)

array([[52, 32,  9],
       [56, 35, 11]])

array([[2., 3.],
       [3., 4.],
       [4., 5.],
       [1., 2.],
       [2., 3.],
       [3., 4.]])

array([[272., 169.,  51.],
       [380., 236.,  71.],
       [488., 303.,  91.],
       [164., 102.,  31.],
       [272., 169.,  51.],
       [380., 236.,  71.]])

array([[[[272., 380., 488.],
         [164., 272., 380.]]],


       [[[169., 236., 303.],
         [102., 169., 236.]]],


       [[[ 51.,  71.,  91.],
         [ 31.,  51.,  71.]]]])

array([[[[102., 206., 195., 102.],
         [125., 230., 204., 113.]]]])

In [8]:
ten_2 = np.array([[[1., 2., 3., 4.],
                 [1., 2., 3., 4.]],
                [[2., 3., 4., 5.],
                 [2., 3., 4., 5.]]])

ten_2 = np.expand_dims(ten_2, 0)
print('ten_2.shape{}'.format(ten_2.shape))
print('ten_2{}'.format(ten_2)) # (1, 2, 2, 4)

kernel = np.array([[[[1., 2., 1.],
                    [1., 1., 1.],
                    [2., 1., 1.]]],
                   [[[2., 1., 1.],
                    [1., 1., 1.],
                    [1., 1., 1.]]]])

kernel = kernel.transpose(3,0,1,2)
print('kernel.shape{}'.format(kernel.shape))
print('kernel{}'.format(kernel))

bias = np.array([[1],[2],[3]])
print('bias.shape{}'.format(bias.shape))

print('bias{}'.format(bias))

ten_2.shape(1, 2, 2, 4)
ten_2[[[[1. 2. 3. 4.]
   [1. 2. 3. 4.]]

  [[2. 3. 4. 5.]
   [2. 3. 4. 5.]]]]
kernel.shape(3, 2, 1, 3)
kernel[[[[1. 1. 2.]]

  [[2. 1. 1.]]]


 [[[2. 1. 1.]]

  [[1. 1. 1.]]]


 [[[1. 1. 1.]]

  [[1. 1. 1.]]]]
bias.shape(3, 1)
bias[[1]
 [2]
 [3]]


In [9]:
dnn3 = Conv2d()
dnn3.forward(ten_2,kernel,bias)

array([[1., 2., 3., 2., 3., 4.],
       [2., 3., 4., 3., 4., 5.],
       [1., 2., 3., 2., 3., 4.],
       [2., 3., 4., 3., 4., 5.]])

array([[1., 2., 1.],
       [1., 1., 1.],
       [2., 1., 1.],
       [2., 1., 1.],
       [1., 1., 1.],
       [1., 1., 1.]])

array([[20., 16., 15.],
       [28., 23., 21.],
       [20., 16., 15.],
       [28., 23., 21.]])

array([[21., 18., 18.],
       [29., 25., 24.],
       [21., 18., 18.],
       [29., 25., 24.]])

(1, 3, 2, 2)

array([[[[21., 29.],
         [21., 29.]],

        [[18., 25.],
         [18., 25.]],

        [[18., 24.],
         [18., 24.]]]])

In [10]:
loss_2 = np.array([[[[9., 11.],
                   [9., 11.]],
                  [[32., 35.],
                   [32., 35.]],
                  [[52., 56.],
                   [52., 56.]]]])
display(loss_2.shape)
dnn3.backward(loss_2)

(1, 3, 2, 2)

array([[ 9., 32., 52.],
       [11., 35., 56.],
       [ 9., 32., 52.],
       [11., 35., 56.]])

array([[1., 2., 1., 2.],
       [2., 3., 2., 3.],
       [3., 4., 3., 4.],
       [2., 3., 2., 3.],
       [3., 4., 3., 4.],
       [4., 5., 4., 5.]])

array([[ 62., 204., 328.],
       [102., 338., 544.],
       [142., 472., 760.],
       [102., 338., 544.],
       [142., 472., 760.],
       [182., 606., 976.]])

array([[[[ 62., 102., 142.]],

        [[102., 142., 182.]]],


       [[[204., 338., 472.]],

        [[338., 472., 606.]]],


       [[[328., 544., 760.]],

        [[544., 760., 976.]]]])

array([[[[125., 230., 204., 113.],
         [125., 230., 204., 113.]],

        [[102., 206., 195., 102.],
         [102., 206., 195., 102.]]]])

【問題3】最大プーリング層の作成 
最大プーリング層のクラスMaxPool2Dを作成してください。
プーリング層は数式で表さない方が分かりやすい部分もありますが、数式で表すとフォワードプロパゲーションは以下のようになります。

In [58]:
class Pooling:
    """
    ノード数n_nodes1からn_nodes2への全結合層
    Parameters
    ----------
    n_nodes1 : int
      前の層のノード数
    n_nodes2 : int
      後の層のノード数
    initializer : 初期化方法のインスタンス
    optimizer : 最適化手法のインスタンス
    """
    def __init__(self, PH ,PW):
        self.P = 0
        self.Str = 2
        self.PH = PH
        self.PW = PW
        
    def forward(self, X):
        """
        フォワード
        Parameters
        ----------
        X : 次の形のndarray, shape (batch_size, n_nodes_bf)
            入力
        Returns
        ----------
        A : 次の形のndarray, shape (batch_size, n_nodes_af)
            出力
        """
        self.X = X
        self.XN, self.XC, self.XH, self.XW = self.X.shape
        #self.X = self.X.transpose(1,0,2,3)
        self.Xre = self.X.reshape(-1, 1, self.XH, self.XW)
        self.pcol = im2col(self.Xre , self.PH, self.PW, self.Str, self.P)
        #display(self.pcol)
        self.p_index = np.argmax(self.pcol, axis=1)
        #display(self.p_index)
        self.p_out_re =np.max(self.pcol,axis=1)
        #display(self.p_out_re)
        self._out_psize()
        self.p_out = self.p_out_re.reshape(self.XN, self.Phout, self.Pwout,-1).transpose(0,3,1,2)
        self.p_out = self.p_out_re.reshape(self.XN, -1, self.Phout, self.Pwout)
        #display(self.pcol)
        
        return self.p_out
    
    def _out_psize(self):
        self.Phout = int((self.XH + 2*self.P - self.PH) / self.Str + 1)       
        self.Pwout = int((self.XW + 2*self.P - self.PW) / self.Str + 1)
    
    def backward(self, dPin):
        """
        バックワード
        Parameters
        ----------
        dA : 次の形のndarray, shape (batch_size, n_nodes2)
            後ろから流れてきた勾配
        Returns
        ----------
        dZ : 次の形のndarray, shape (batch_size, n_nodes1)
            前に流す勾配
        """
        self.dPre = dPin.reshape(1,-1)
        self.backP = np.zeros((self.pcol.shape)) 
        for i in range(len(self.p_index)):
            self.backP[i][self.p_index[i]] = self.dPre[:,i]
        #display(self.backP)
        #display(self.pcol)
        self.dbackP = col2im(self.backP, self.Xre.shape, self.PH, self.PW, self.Str, self.P)
        self.dbackP = self.dbackP.reshape(self.X.shape)
        return self.dbackP

In [59]:
xin = np.array([[[[1,3,2,9],
                  [7,4,1,5],
                  [8,5,2,3],
                  [4,2,1,4]],
                 
                 [[1,3,2,9],
                  [7,4,1,5],
                  [8,5,2,3],
                  [4,2,1,4]]],
               [[[1,3,2,9],
                  [7,4,1,5],
                  [8,5,2,3],
                  [4,2,1,4]],
                 
                 [[1,3,2,9],
                  [7,4,1,5],
                  [8,5,2,3],
                  [4,2,1,4]]]])
display(xin.shape)
scr_pool=Pooling(2,2)
scr_pool.forward(xin).shape

(2, 2, 4, 4)

(2, 2, 2, 2)

In [60]:
#dP = np.array([[[[1,2,3],
#                 [4,5,6],
#                 [7,8,9]]]])
dP = np.array([[[[1,2],
                 [3,4]],
                
                [[1,2],
                 [3,4]]],
              [[[1,2],
                 [3,4]],
                
                [[1,2],
                 [3,4]]]])
display(dP.shape)
scr_pool.backward(dP)

(2, 2, 2, 2)

array([[[[0., 0., 0., 2.],
         [1., 0., 0., 0.],
         [3., 0., 0., 0.],
         [0., 0., 0., 4.]],

        [[0., 0., 0., 2.],
         [1., 0., 0., 0.],
         [3., 0., 0., 0.],
         [0., 0., 0., 4.]]],


       [[[0., 0., 0., 2.],
         [1., 0., 0., 0.],
         [3., 0., 0., 0.],
         [0., 0., 0., 4.]],

        [[0., 0., 0., 2.],
         [1., 0., 0., 0.],
         [3., 0., 0., 0.],
         [0., 0., 0., 4.]]]])

【問題5】平滑化 
平滑化するためのFlattenクラスを作成してください。
フォワードのときはチャンネル、高さ、幅の3次元を1次元にreshapeします。
その値は記録しておき、バックワードのときに再びreshapeによって形を戻します。
この平滑化のクラスを挟むことで出力前の全結合層に適した配列を作ることができます。

In [14]:
class Flatten:
    """
    ノード数n_nodes1からn_nodes2への全結合層
    Parameters
    ----------
    n_nodes1 : int
      前の層のノード数
    n_nodes2 : int
      後の層のノード数
    initializer : 初期化方法のインスタンス
    optimizer : 最適化手法のインスタンス
    """
    def forward(self, X):
        """
        フォワード
        Parameters
        ----------
        X : 次の形のndarray, shape (batch_size, n_nodes_bf)
            入力
        Returns
        ----------
        A : 次の形のndarray, shape (batch_size, n_nodes_af)
            出力
        """
        self.XN, self.XC, self.XH, self.XW = X.shape
        self.flatout = X.reshape(self.XN,-1)
        
        return self.flatout
    
    def backward(self, dPin):
        """
        バックワード
        Parameters
        ----------
        dA : 次の形のndarray, shape (batch_size, n_nodes2)
            後ろから流れてきた勾配
        Returns
        ----------
        dZ : 次の形のndarray, shape (batch_size, n_nodes1)
            前に流す勾配
        """
        self.dFlatten = dPin.reshape(self.XN, self.XC, self.XH, self.XW )
        
        return self.dFlatten

In [15]:
scr_flatten = Flatten()
scr_flatten.forward(dnn2.forward(x,w,b)) 

array([[2., 3., 4., 1., 2., 3.],
       [3., 4., 5., 2., 3., 4.]])

array([[1, 1, 2],
       [1, 1, 1],
       [1, 1, 1],
       [1, 2, 1],
       [1, 1, 1],
       [1, 1, 2]])

array([[15., 16., 20.],
       [21., 23., 28.]])

array([[18., 18., 21.],
       [24., 25., 29.]])

(1, 3, 1, 2)

array([[18., 24., 18., 25., 21., 29.]])

In [16]:
deluta_flat = np.array([1,2,3,4,5,6])
scr_flatten.backward(deluta_flat) 

array([[[[1, 2]],

        [[3, 4]],

        [[5, 6]]]])

【問題6】学習と推定 
作成したConv2dを使用してMNISTを学習・推定し、Accuracyを計算してください。
精度は低くともまずは動くことを目指してください。

In [17]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import math
from sklearn.metrics import accuracy_score
from sklearn import metrics
from sklearn.metrics import confusion_matrix

In [18]:
from keras.datasets import mnist
(X_train, y_train), (X_test, y_test) = mnist.load_data()

C:\Users\anai\Anaconda3\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.
C:\Users\anai\AppData\Roaming\Python\Python36\site-packages\tensorflow\python\framework\dtypes.py:516: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
C:\Users\anai\AppData\Roaming\Python\Python36\site-packages\tensorflow\python\framework\dtypes.py:517: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
C:\Users\anai\AppData\Roaming\Python\P

In [19]:
X_train = X_train.astype(np.float)
X_test = X_test.astype(np.float)
X_train /= 255
X_test /= 255

X_train = X_train[:, np.newaxis,:,:]
X_test = X_test[:, np.newaxis,:,:]

from sklearn.preprocessing import OneHotEncoder
enc = OneHotEncoder(handle_unknown='ignore', sparse=False)
y_train_one_hot = enc.fit_transform(y_train[:, np.newaxis])
y_test_one_hot = enc.transform(y_test[:, np.newaxis])

from sklearn.model_selection import train_test_split
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train_one_hot, test_size=0.2)

In [20]:
class GetMiniBatch:
    """
    ミニバッチを取得するイテレータ

    Parameters
    ----------
    X : 次の形のndarray, shape (n_samples, n_features)
      訓練用データ
    y : 次の形のndarray, shape (n_samples, 1)
      正解値
    batch_size : int
      バッチサイズ
    seed : int
      NumPyの乱数のシード
    """
    def __init__(self, X, y, batch_size = 20, seed=0):
        self.batch_size = batch_size
        np.random.seed(seed)
        shuffle_index = np.random.permutation(np.arange(X.shape[0]))
        self._X = X[shuffle_index]
        self._y = y[shuffle_index]
        self._stop = np.ceil(X.shape[0]/self.batch_size).astype(np.int)

    def __len__(self):
        return self._stop

    def __getitem__(self,item):
        p0 = item*self.batch_size
        p1 = item*self.batch_size + self.batch_size
        return self._X[p0:p1], self._y[p0:p1]        

    def __iter__(self):
        self._counter = 0
        return self

    def __next__(self):
        if self._counter >= self._stop:
            raise StopIteration()
        p0 = self._counter*self.batch_size
        p1 = self._counter*self.batch_size + self.batch_size
        self._counter += 1
        return self._X[p0:p1], self._y[p0:p1]

In [21]:
class SimpleInitializer:
    """
    ガウス分布によるシンプルな初期化
    Parameters
    ----------
    sigma : float
      ガウス分布の標準偏差
    """
    def __init__(self, sigma):
        self.sigma = sigma
        #display(self.sigma.Calc)
    def W(self, FC, FN, FH=3, FW=3):
        """
        重みの初期化
        Parameters
        ----------
        n_nodes1 : int
          前の層のノード数
        n_nodes2 : int
          後の層のノード数

        Returns
        ----------
        W :
        """
        W = self.sigma * np.random.randn(FN, FC, FH, FW)
        return W
    
    def B(self, FN):
        """
        バイアスの初期化
        Parameters
        ----------
        n_nodes2 : int
          後の層のノード数

        Returns
        ----------
        B :
        """
        B = self.sigma * np.random.randn(1, FN)
        return B

In [22]:
class SGD:
    """
    確率的勾配降下法
    Parameters
    ----------
    lr : 学習率
    """
    def __init__(self, lr):
        self.lr = lr

    def update(self, dWorB, WorB):
        """
        ある層の重みやバイアスの更新
        Parameters
        ----------
        layer : 更新前の層のインスタンス

        Returns
        ----------
        layer : 更新後の層のインスタンス
        """
        self.WorB = WorB
        self.WorB -= self.lr*dWorB
        return self.WorB

In [23]:
class Activation:
    """
    活性化関数　tanh
    Parameters
    ----------
    """
    def __init__(self):
        pass
    def tanh_fw(self, X):
        """
        フォワード
        Parameters
        ----------
        X : 次の形のndarray, shape (batch_size, n_nodes_bf)
            入力
        Returns
        ----------
        A : 次の形のndarray, shape (batch_size, n_nodes_af)
            出力
        """     
        self.A = X
        Z = np.tanh(X)
        return Z

    def tanh_bw(self, dZ):
        """
        バックワード
        Parameters
        ----------
        dA : 次の形のndarray, shape (batch_size, n_nodes2)
            後ろから流れてきた勾配
        Returns
        ----------
        dZ : 次の形のndarray, shape (batch_size, n_nodes1)
            前に流す勾配
        """
        dA = dZ * (1 - np.tanh(self.A)**2)  
        return dA
    
    def softmax_fw(self, X, y):
        """
        フォワード
        Parameters
        ----------
        X : 次の形のndarray, shape (batch_size, n_nodes_bf)
            入力
        Returns
        ----------
        A : 次の形のndarray, shape (batch_size, n_nodes_af)
            出力
        """     
        Z = np.exp(X) / np.sum(np.exp(X), axis=1).reshape(-1,1)
        return Z

    def softmax_bw(self, Z, y):
        """
        バックワード
        Parameters
        ----------
        dA : 次の形のndarray, shape (batch_size, n_nodes2)
            後ろから流れてきた勾配
        Returns
        ----------
        dZ : 次の形のndarray, shape (batch_size, n_nodes1)
            前に流す勾配
        """
        dA = Z - y
        return dA

    def entropy(self, Z, y):
        """
        フォワード
        Parameters
        ----------
        X : 次の形のndarray, shape (batch_size, n_nodes_bf)
            入力
        Returns
        ----------
        A : 次の形のndarray, shape (batch_size, n_nodes_af)
            出力
        """     
        L = -1*np.average(np.sum(y * np.log(Z), axis=1), axis=0)
        return L

In [24]:
class Xavier:
    """
    活性化関数　tanh
    Parameters
    ----------
    """
    def __init__(self,n):
        self.n=n
        self.calc = 1/np.sqrt(self.n)

In [25]:
class FC:
    """
    ノード数n_nodes1からn_nodes2への全結合層
    Parameters
    ----------
    n_nodes1 : int
      前の層のノード数
    n_nodes2 : int
      後の層のノード数
    initializer : 初期化方法のインスタンス
    optimizer : 最適化手法のインスタンス
    """
    def __init__(self, n_nodes1, n_nodes2, sigma, optimizer):
        # 初期化
        # initializerのメソッドを使い、self.Wとself.Bを初期化する
        self.n_nodes1 = n_nodes1
        self.n_nodes2 = n_nodes2
        self.optimizer = optimizer
        #self.W = initializer.W(self.n_nodes1, self.n_nodes2)
        #self.B = initializer.B(self.n_nodes2)
        display(sigma)
        self.W = sigma * np.random.randn(self.n_nodes1, self.n_nodes2)
        self.B = sigma * np.random.randn(1, self.n_nodes2)
        
    def forward(self, X):
        """
        フォワード
        Parameters
        ----------
        X : 次の形のndarray, shape (batch_size, n_nodes_bf)
            入力
        Returns
        ----------
        A : 次の形のndarray, shape (batch_size, n_nodes_af)
            出力
        """
        self.X = X
        #display(self.X.shape)
        #display(self.W.shape)
        #display(self.B.shape)
        A = np.dot(self.X, self.W) +  self.B
        #display(A.shape)
        return A

    def backward(self, dA):
        """
        バックワード
        Parameters
        ----------
        dA : 次の形のndarray, shape (batch_size, n_nodes2)
            後ろから流れてきた勾配
        Returns
        ----------
        dZ : 次の形のndarray, shape (batch_size, n_nodes1)
            前に流す勾配
        """
        dB = np.sum(dA, axis=0)
        dW = np.dot(self.X.T, dA)
        dZ = np.dot(dA, self.W.T)     

        # 更新
        #self = self.optimizer.update(dW, dB, self.W, self.W)
        self.W = self.optimizer.update(dW, self.W)
        self.B = self.optimizer.update(dB, self.B)

        return dZ


In [63]:
class Conv2d:
    """
    ノード数n_nodes1からn_nodes2への全結合層
    Parameters
    ----------
    n_nodes1 : int
      前の層のノード数
    n_nodes2 : int
      後の層のノード数
    initializer : 初期化方法のインスタンス
    optimizer : 最適化手法のインスタンス
    """
    def __init__(self, initializer, optimizer, FC, FN, FH=3, FW=3):
        self.P = 0
        self.Str = 1
        self.optimizer = optimizer
        self.W = initializer.W(FC, FN)
        self.B = initializer.B(FN)

        self.a = np.array([])
        self.dW = np.array([])
        self.dX = np.array([])
        #self.s=None
        
    def forward(self, X):
        """
        フォワード
        Parameters
        ----------
        X : 次の形のndarray, shape (batch_size, n_nodes_bf)
            入力
        Returns
        ----------
        A : 次の形のndarray, shape (batch_size, n_nodes_af)
            出力
        """
        self.X = X
        self.XN, self.XC, self.XH, self.XW = self.X.shape
        self.FN, self.FC, self.FH, self.FW = self.W.shape
        self.s = self.W.shape[3]
        
        self._output_size()
        
        self.Wre = self.W.reshape(self.FN,-1)
        self.Bre = self.B.reshape(1,-1)
        self.col = im2col(self.X , self.FH, self.FW, self.Str, self.P)
        
        self.Are = (self.col @ self.Wre.T) + self.Bre
        self.a = self.Are.reshape(self.XN, self.Nhout, self.Nwout,-1).transpose(0,3,1,2)

        return self.a
    
    def _output_size(self):
        self.Nhout = int((self.XH + 2*self.P - self.FH) / self.Str + 1)       
        self.Nwout = int((self.XW + 2*self.P - self.FW) / self.Str + 1)
        
    def backward(self, dA):
        """
        バックワード
        Parameters
        ----------
        dA : 次の形のndarray, shape (batch_size, n_nodes2)
            後ろから流れてきた勾配
        Returns
        ----------
        dZ : 次の形のndarray, shape (batch_size, n_nodes1)
            前に流す勾配
        """
        self.dA=dA.transpose(0,2,3,1).reshape(-1,self.FN)
        self.dB = np.sum(self.dA, axis=0)
        
        self.dW = np.dot(self.col.T , self.dA)
        self.dW = self.dW.transpose(1, 0).reshape(self.FN, self.FC, self.FH, self.FW)
        
        self.dXre = np.dot(self.dA, self.Wre) 
        self.dX = col2im(self.dXre, self.X.shape, self.FH, self.FW, self.Str, self.P)

        self.W = self.optimizer.update(self.dW, self.W)
        self.B = self.optimizer.update(self.dB, self.B)
        
        return self.dX
    

In [66]:
class ScratchSimpleNeuralNetrowkClassifier():
    """
    シンプルな三層ニューラルネットワーク分類器

    Parameters
    ----------
    bp : int
        バックプロパゲーション回数
    Attributes
    ----------
    """
    def __init__(self, how_prp="htan", FN1=3, FN2=6, n_output=10, n_epoq=5, batch_size=20, 
                 lr=0.001, verbose = True):
        self.n_epoq = n_epoq
        self.FN1 = FN1
        self.FN2 = FN2
        self.n_output = n_output
        self.batch_size = batch_size
        self.how_prp = how_prp
        self.lr = lr
        self.loss_list = np.array([])
        self.loss_val_list = np.array([])

    def fit(self, X, y):
        """
        ニューラルネットワーク分類器を学習する。
        Parameters
        ----------
        X : 次の形のndarray, shape (n_samples, n_features)
            訓練用データの特徴量
        y : 次の形のndarray, shape (n_samples, )
            訓練用データの正解値
        """
        self.X = X
        self.XN, self.XC, self.XH, self.XW = self.X.shape
        
        optimizer = SGD(self.lr)
        sigma1=Xavier(self.XC*3*3)
        sigma2=Xavier(self.FN1*3*3)
        
        flatten_node = self.FN2*5*5
        #last_node = np.round(flatten_node/2).astype(int)
        sigma3=Xavier(self.n_output)
        
        self.CONV1 = Conv2d(SimpleInitializer(sigma1.calc), optimizer, self.XC, self.FN1, FH=3, FW=3)
        self.activation1 = Activation()
        self.MaxPool1 = Pooling(PH=2,PW=2)
        self.CONV2 = Conv2d(SimpleInitializer(sigma2.calc), optimizer, self.FN1, self.FN2, FH=3, FW=3)
        self.activation2 = Activation()
        self.MaxPool2 = Pooling(PH=2,PW=2)
        self.FLAT = Flatten()
        self.DENSE = FC(flatten_node, self.n_output, sigma3.calc, optimizer)
        self.activation3 = Activation()
        
        self.val = 0
        get_mini_batch = GetMiniBatch(X, y, batch_size=self.batch_size)
        for _ in range(self.n_epoq):
            for X_mini, y_mini in get_mini_batch:
                self.X_ = X_mini
                self.y_ = y_mini
                display(sigma3)
                self._forward_propagation(self.X_)
                self._back_propagation()
                
            self.L = self.activation3.entropy(self.Z3, self.y_)        
            self.loss_list = np.append(self.loss_list, self.L)
        
    def _forward_propagation(self, X):
        self.a1 = self.CONV1.forward(X)
        self.Z1 = self.activation1.tanh_fw(self.a1)
        display(self.Z1.shape)
        self.p1 = self.MaxPool1.forward(self.Z1)
        display(self.p1.shape)
        self.a2 = self.CONV2.forward(self.p1)
        display(self.a2.shape)
        self.Z2 = self.activation2.tanh_fw(self.a2)
        display(self.Z2.shape)
        self.p2 = self.MaxPool2.forward(self.Z2)
        display(self.p2.shape)
        self.flat = self.FLAT.forward(self.p2) 
        display(self.flat.shape)
        
        self.den = self.DENSE.forward(self.flat)
        display(self.den.shape)
        self.Z3 = self.activation3.softmax_fw(self.den, self.y_)
        display(self.Z3.shape)
        
    def _back_propagation(self):
        dA3 = self.activation3.softmax_bw(self.Z3, self.y_)
        display(dA3.shape)
        dZ2 = self.DENSE.backward(dA3)
        display(dZ2.shape)
        dflat = self.FLAT.backward(dZ2)
        display(dflat.shape)
        dP2 = self.MaxPool2.backward(dflat)
        display(dP2.shape)
        dA2 = self.activation2.tanh_bw(dP2)
        dZ1 = self.CONV2.backward(dA2)
        
        dP1 = self.MaxPool1.backward(dZ1)
        dA1 = self.activation1.tanh_bw(dP1)
        #dZ0 = self.CONV2.backward(dA1)        

    def graph_cost_func(self):
        """
        損失の推移をグラフ化する。    
        検証用データが入力されていれば、学習用と検証用の損失推移を重ねてグラフ化
        """
        plt.title("Num_of_Epoq vs Loss")
        plt.xlabel("Num_of_Epoq")
        plt.ylabel("Loss")
        plt.plot(range(1,self.n_epoq+1), self.loss_list, color="b", marker="o", label="train_loss")
        plt.grid()
        plt.legend()
        plt.show()
  
    def predict(self, X):
        """
        ニューラルネットワーク分類器を使い推定する。
        Parameters
        ----------
        X : 次の形のndarray, shape (n_samples, n_features)
            サンプル
            
        Returns
        -------
            次の形のndarray, shape (n_samples, 1)
            推定結果
        """
        pred_y =self._forward_propagation(X)

        return np.argmax(pred_y, axis=1)

In [ ]:
scr_nnc = ScratchSimpleNeuralNetrowkClassifier(batch_size=100)
scr_nnc.fit(X_train, y_train)

0.31622776601683794

(100, 3, 26, 26)

(100, 3, 13, 13)

(100, 6, 11, 11)

(100, 6, 11, 11)

...

(100, 3, 26, 26)

(100, 3, 13, 13)

(100, 6, 11, 11)

(100, 6, 11, 11)

(100, 6, 5, 5)

In [ ]:
scr_nnc.predict(X_val)

In [ ]:
from sklearn.metrics import accuracy_score
from sklearn import metrics
from sklearn.metrics import confusion_matrix

print("accuracy:{}".format(accuracy_score(y_test, scr_nnc.predict(X_test))))
print(" {}".format(confusion_matrix(y_test, scr_nnc.predict(X_test))))

In [ ]:
scr_nnc.graph_cost_func()